In [2]:
import time
import random
import cProfile

import matplotlib.pyplot as plt
import osmnx as ox
import networkx as nx
import folium

from routers import time_dependent_dijkstra, single_source_time_dependent_dijkstra
from converters import *
from functions import *
from loaders import create_GTFS_graph
from other import plot_path_browser
from functions import create_service_area

Задаем константы


In [3]:
GTFSpath = r"D:\Python_progs\Feeds\Klapeida" # Путь к папке с GTFS файлами
departure_time_input = "18:00:00" # Время отправления в формате HH:MM:SS
day = 'monday' # День недели
time_zero = time.time()

plot_graph = False # Не работает
save_city_graph = False # Сохранять граф города в файл
plot_path_in_browser = False # Отобразить маршрут при помощи Folium в браузере
plot_path_folium = True # Отобразить маршрут при помощи Folium в Ipython Notebook

Загружаем комбинированный граф GTFS и OSM

In [4]:
G_combined, city_name, departure_time_seconds, stops = create_GTFS_graph(GTFSpath, departure_time_input, 
                                                                         day, 
                                                                         duration_seconds=3600*3, 
                                                                         save_to_csv = True)

GTFS data loaded
12181 of 72974 trips retained
Выпуклая оболочка построена
Граф улиц загружен
Число узлов: 32002
Число ребер: 83167
Соединение завершено


Выбираем рандомные узлы графа для расчета времени в пути. 
По координатам потом удобно сверять время с Гугл картами/Яндексом  

p.s. Главное отключить метро :) 
p.p.s В гугл картах лучше сравнивать не время в пути, а время прибытия, т.к. они не показывают время ожидания



In [14]:
source = random.choice(list(G_combined.nodes))
target = random.choice(list(G_combined.nodes))

print("Source: ", source, "coordinates", G_combined.nodes[source]['y'], G_combined.nodes[source]['x'])
print("Target: ", target, "coordinates", G_combined.nodes[target]['y'], G_combined.nodes[target]['x'])

Source:  4732460849 coordinates 55.7049653 21.1761777
Target:  1865281370 coordinates 55.772602 21.0857239


In [15]:
def main():
    sample_time = time.time()
    
    path, arrival_time, travel_time, used_routes = time_dependent_dijkstra(
                            graph = G_combined, 
                            source = source, 
                            target = target, 
                            start_time = parse_time_to_seconds(departure_time_input),
                            track_used_routes=True,
                        )

    #print(f"Path: {path}")
    print('Used routes:', used_routes)
    print(f"Arrival time at destination: {parse_seconds_to_time(arrival_time)} in {parse_seconds_to_time(travel_time)}")

    print(f"Time elapsed: {time.time() - sample_time} seconds")

    return path, arrival_time, travel_time

path, arrival_time, travel_time = main()

Used routes: {None, 'klaipeda_bus_5', 'klaipeda_bus_3', 'klaipeda_bus_6', 'klaipeda_bus_4'}
Arrival time at destination: 19:14:39 in 01:14:39
Time elapsed: 0.28757476806640625 seconds


In [16]:
G_path = nx.subgraph(G_combined, path)

graph = nx.MultiDiGraph(G_path)

G_nodes, G_edges = ox.graph_to_gdfs(graph)

frame_center_lat = stops['stop_lat'].mean()
frame_center_lon = stops['stop_lon'].mean()

if plot_path_in_browser:
    plot_path_browser(graph, stops)

m2 = folium.Map(location=[frame_center_lat, frame_center_lon], 
                zoom_start=12,
                width='100%', height='100%')

G_edges.explore(m = m2)

G_nodes.explore(m = m2,
                column = 'type',
                cmap = 'rainbow')

In [17]:
print(G_edges.info())


<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 91 entries, (7573141504.0, 3455263152.0, 0) to (450288764.0, 8001050483.0, 0)
Data columns (total 15 columns):
 #   Column            Non-Null Count  Dtype   
---  ------            --------------  -----   
 0   osmid             70 non-null     object  
 1   ref               22 non-null     object  
 2   name              56 non-null     object  
 3   highway           70 non-null     object  
 4   maxspeed          62 non-null     object  
 5   oneway            70 non-null     object  
 6   reversed          70 non-null     object  
 7   length            70 non-null     float64 
 8   weight            78 non-null     float64 
 9   geometry          91 non-null     geometry
 10  lanes             10 non-null     object  
 11  schedules         13 non-null     object  
 12  sorted_schedules  13 non-null     object  
 13  type              8 non-null      object  
 14  service           2 non-null      object  
dtypes: float64

In [18]:
sa_source = random.choice(list(G_combined.nodes))

In [19]:
polygon, points = create_service_area(G_combined, sa_source, parse_time_to_seconds(departure_time_input), 3600, buffer_radius=100)

In [20]:
import shapely.geometry

point = shapely.geometry.Point(G_combined.nodes[sa_source]['x'], G_combined.nodes[sa_source]['y'])
point_gdf = gpd.GeoDataFrame(geometry=[point])

frame_center_lat = stops['stop_lat'].mean()
frame_center_lon = stops['stop_lon'].mean()

m = folium.Map(location=[frame_center_lat, frame_center_lon], 
                zoom_start=12,
                width='100%', height='100%')

polygon.explore(m = m)
point_gdf.explore(m = m, color = 'red')


In [21]:
'''def main():
    G_combined, city_name, departure_time_seconds, stops = create_GTFS_graph(GTFSpath, departure_time_input, 
                                                                            day, 
                                                                            duration_seconds=3600*3, 
                                                                            save_to_csv = True)

cProfile.run("main()")'''

'def main():\n    G_combined, city_name, departure_time_seconds, stops = create_GTFS_graph(GTFSpath, departure_time_input, \n                                                                            day, \n                                                                            duration_seconds=3600*3, \n                                                                            save_to_csv = True)\n\ncProfile.run("main()")'

In [22]:
"""times_list = []
startt = parse_time_to_seconds(departure_time_input)
endt = startt + 3600
for i in range(startt, endt, 360):
    try:
        path, arrival_time, travel_time, used_routes = time_dependent_dijkstra_2(
                                        graph = G_combined, 
                                        source = source, 
                                        target = target, 
                                        start_time = i,
                                        track_used_routes=True)
                                    
        times_list.append(tuple([i, travel_time]))
    except:
        continue
    
print(times_list)

plt.figure(figsize=(14,7))
plt.plot(*zip(*times_list))

plt.xlabel('Departure Time')
plt.ylabel('Travel Time')
plt.show()"""

"times_list = []\nstartt = parse_time_to_seconds(departure_time_input)\nendt = startt + 3600\nfor i in range(startt, endt, 360):\n    try:\n        path, arrival_time, travel_time, used_routes = time_dependent_dijkstra_2(\n                                        graph = G_combined, \n                                        source = source, \n                                        target = target, \n                                        start_time = i,\n                                        track_used_routes=True)\n                                    \n        times_list.append(tuple([i, travel_time]))\n    except:\n        continue\n    \nprint(times_list)\n\nplt.figure(figsize=(14,7))\nplt.plot(*zip(*times_list))\n\nplt.xlabel('Departure Time')\nplt.ylabel('Travel Time')\nplt.show()"